<a href="https://colab.research.google.com/github/zhulkhoirrifat/Email-Classification-MLPipline/blob/main/pipeline.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Email Spam Classification

In [1]:
!python --version

Python 3.10.12


In [ ]:
!pip install -U tensorflow==2.13.0 tfx==1.14.0 wheel==0.43.0 setuptools==69.5.1

In [7]:
import pandas as pd
df = pd.read_csv('data/emails.csv')
df

text  spam
0     Subject: naturally irresistible your corporate...     1
1     Subject: the stock trading gunslinger  fanny i...     1
2     Subject: unbelievable new homes made easy  im ...     1
3     Subject: 4 color printing special  request add...     1
4     Subject: do not have money , get software cds ...     1
...                                                 ...   ...
5723  Subject: re : research and development charges...     0
5724  Subject: re : receipts from visit  jim ,  than...     0
5725  Subject: re : enron case study update  wow ! a...     0
5726  Subject: re : interest  david ,  please , call...     0
5727  Subject: news : aurora 5 . 2 update  aurora ve...     0

[5728 rows x 2 columns]

## Import Library

In [3]:
import os
import tensorflow as tf
from tfx.components import CsvExampleGen, StatisticsGen, SchemaGen, ExampleValidator, Transform, Trainer, Tuner
from tfx.proto import example_gen_pb2
from tfx.orchestration.experimental.interactive.interactive_context import InteractiveContext

## Set Variable

In [4]:
PIPLINE_NAME = 'mushroom-pipline'
SCHEMA_PIPLINE_NAME = 'mushroom-tfdv-schema'

# Directory menyimpan artifact
PIPLINE_ROOT = os.path.join('piplines', PIPLINE_NAME)

# Path ke SQLite DB untuk digunakan sebagai MLMD storage
METADATA_PATH = os.path.join('metadata', PIPLINE_NAME, 'metadata.db')

# Direktori output dimana model yang dibuat dari pipline akan di ekspor
SERVING_MODEL_DIR = os.path.join('serving-model', PIPLINE_NAME)


In [5]:
DATA_ROOT = 'data'

interactive_context = InteractiveContext(pipeline_root=PIPLINE_ROOT)

### Data Ingestion

In [6]:
output = example_gen_pb2.Output(
    split_config = example_gen_pb2.SplitConfig(splits=[
        example_gen_pb2.SplitConfig.Split(name='train', hash_buckets=8),
        example_gen_pb2.SplitConfig.Split(name='eval', hash_buckets=2)
    ])
)
example_gen = CsvExampleGen(input_base=DATA_ROOT, output_config=output)
interactive_context.run(example_gen)

ExecutionResult(
    component_id: CsvExampleGen
    execution_id: 1
    outputs:
        examples: OutputChannel(artifact_type=Examples, producer_component_id=CsvExampleGen, output_key=examples, additional_properties={}, additional_custom_properties={}, _input_trigger=None)

## Data Validation

### Summary Statistic (StatisticGen)

In [7]:
statistics_gen = StatisticsGen(
    examples=example_gen.outputs['examples']
)
interactive_context.run(statistics_gen)

ExecutionResult(
    component_id: StatisticsGen
    execution_id: 2
    outputs:
        statistics: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=StatisticsGen, output_key=statistics, additional_properties={}, additional_custom_properties={}, _input_trigger=None)

In [8]:
interactive_context.show(statistics_gen.outputs['statistics'])

### Data Schema



In [9]:
schema_gen = SchemaGen(
    statistics=statistics_gen.outputs['statistics']
)
interactive_context.run(schema_gen)

ExecutionResult(
    component_id: SchemaGen
    execution_id: 3
    outputs:
        schema: OutputChannel(artifact_type=Schema, producer_component_id=SchemaGen, output_key=schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None)

In [10]:
interactive_context.show(schema_gen.outputs['schema'])

Type  Presence Valency Domain
Feature name                                
'spam'          INT  required              -
'text'        BYTES  required              -

### Example Validator

In [11]:
example_validator = ExampleValidator(
    statistics=statistics_gen.outputs['statistics'],
    schema=schema_gen.outputs['schema']
)
interactive_context.run(example_validator)

ExecutionResult(
    component_id: ExampleValidator
    execution_id: 4
    outputs:
        anomalies: OutputChannel(artifact_type=ExampleAnomalies, producer_component_id=ExampleValidator, output_key=anomalies, additional_properties={}, additional_custom_properties={}, _input_trigger=None)

In [12]:
interactive_context.show(example_validator.outputs['anomalies'])

## Data Preprocessing

### Transform

In [13]:
TRANSFORM_MODULE_FILE = "modules/transform.py"

In [14]:
%%writefile {TRANSFORM_MODULE_FILE}
import string
import tensorflow as tf
import tensorflow_transform as tft

LABEL_KEY = 'spam'
FEATURE_KEY = 'text'


def transformed_name(key):
  """ Transform feature key

  Args:
    key(str): the key has to be transformed

  Returns:
    str: transformed key
  """

  return f"{key}_xf"


def preprocessing_fn(inputs):
  """Preprocess input features into transformed features

    Args:
      inputs (dict): map from feature keys to raw features

    Returns:
      dict: map from features keys to transformed features
  """

  outputs = {}

  outputs[transformed_name(FEATURE_KEY)] = tf.strings.lower(inputs[FEATURE_KEY])
  outputs[transformed_name(LABEL_KEY)] = tf.cast(inputs[LABEL_KEY], tf.int64)

  return outputs

Writing modules/transform.py


In [15]:
transform = Transform(
    examples=example_gen.outputs["examples"],
    schema=schema_gen.outputs["schema"],
    module_file=os.path.abspath(TRANSFORM_MODULE_FILE)
)
interactive_context.run(transform)

ExecutionResult(
    component_id: Transform
    execution_id: 5
    outputs:
        transform_graph: OutputChannel(artifact_type=TransformGraph, producer_component_id=Transform, output_key=transform_graph, additional_properties={}, additional_custom_properties={}, _input_trigger=None
        transformed_examples: OutputChannel(artifact_type=Examples, producer_component_id=Transform, output_key=transformed_examples, additional_properties={}, additional_custom_properties={}, _input_trigger=None
        updated_analyzer_cache: OutputChannel(artifact_type=TransformCache, producer_component_id=Transform, output_key=updated_analyzer_cache, additional_properties={}, additional_custom_properties={}, _input_trigger=None
        pre_transform_schema: OutputChannel(artifact_type=Schema, producer_component_id=Transform, output_key=pre_transform_schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None
        pre_transform_stats: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=Transform, output_key=pre_transform_stats, additional_properties={}, additional_custom_properties={}, _input_trigger=None
        post_transform_schema: OutputChannel(artifact_type=Schema, producer_component_id=Transform, output_key=post_transform_schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None
        post_transform_stats: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=Transform, output_key=post_transform_stats, additional_properties={}, additional_custom_properties={}, _input_trigger=None
        post_transform_anomalies: OutputChannel(artifact_type=ExampleAnomalies, producer_component_id=Transform, output_key=post_transform_anomalies, additional_properties={}, additional_custom_properties={}, _input_trigger=None)

## Training Model

In [16]:
TRAINER_MODULE_FILE = "modules/trainer.py"

In [19]:
%%writefile {TRAINER_MODULE_FILE}
import os
import tensorflow as tf
import tensorflow_transform as tft
from tensorflow.keras import layers
from tfx.components.trainer.fn_args_utils import FnArgs
from transform import (FEATURE_KEY, LABEL_KEY, transformed_name)

def gzip_reader_fn(filenames):
  """ Loads compressed data

  Args:
    filenames(str): Path to the data directory

  Return:
    TfRecord: Compressed data

  """
  return tf.data.TFRecordDataset(filenames, compression_type="GZIP")

def input_fn(file_pattern, tf_transform_output, num_epochs, batch_size=64)->tf.data.Dataset:
  """ Creates a batched dataset from TFRecord file

  Args:
    file_pattern(str): Path pattern to the TFRecord file
    tf_transform_output(tft.TFTransformOutput): Output from TFX transformation
    batch_size(int): Batch size for the dataset

  Returns:
    tf.data.Dataset: Dataset that has been batched and ready for training
  """

  transform_feature_spec = (
      tf_transform_output.transformed_feature_spec().copy()
  )

  dataset = tf.data.experimental.make_batched_features_dataset(
      file_pattern=file_pattern,
      batch_size=batch_size,
      features=transform_feature_spec,
      reader=gzip_reader_fn,
      num_epochs=num_epochs,
      label_key=transformed_name(LABEL_KEY)
  )

  return dataset

VOCAB_SIZE = 10000
SEQUENCE_LENGTH = 100

vectorize_layer = layers.TextVectorization(
    standardize="lower_and_strip_punctuation",
    max_tokens=VOCAB_SIZE,
    output_mode='int',
    output_sequence_length=SEQUENCE_LENGTH
)

embedding_dim=16

def model_builder() :
  """ Build keras model

  Returns:
    tf.keras.Model: Keras Model that has been compiled.
  """
  inputs = tf.keras.Input(shape=(1,), name = transformed_name(FEATURE_KEY), dtype = tf.string)
  reshaped_narrative = tf.reshape(inputs, [-1])
  x = vectorize_layer(reshaped_narrative)
  x = tf.keras.layers.Embedding(VOCAB_SIZE, embedding_dim, name = "embedding")(x)
  x = tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(64, return_sequences=True))(x)
  x = tf.keras.layers.LSTM(64, return_sequences=False)(x)
  x = tf.keras.layers.Dense(64, activation = "relu")(x)
  x = tf.keras.layers.Dropout(0.2)(x)
  x = tf.keras.layers.Dense(32, activation = "relu")(x)
  outputs = tf.keras.layers.Dense(1, activation = "sigmoid")(x)

  model = tf.keras.Model(inputs = inputs, outputs = outputs)

  model.compile(
      loss = 'binary_crossentropy',
      optimizer = tf.keras.optimizers.Adam(0.01),
      metrics = [tf.keras.metrics.BinaryAccuracy()]
  )

  model.summary()
  return model

def get_serve_tf_examples_fn(model, tf_transform_output):
  """ Return a function that parses a serialized tf.Example and applies TFT

  Args:
    model(tf.keras.Model): The model to be used for serving.
    tf_transform_output(tft.TFTransformOutput): Output of the TFX Transformation

  Returns
    serve_tf_examples_fn(function): Function that processes the serialized input tf.Example and returns the model output
  """

  model.tft_layer = tf_transform_output.transform_features_layer()

  @tf.function
  def serve_tf_examples_fn(serialized_tf_examples):
    """ Parse and transform serialized tf.Example data, then return model predictions

    Args:
      serialized_tf_examples(tf.Tensor): A batch of serialized tf.Example data

    Returns:
      predictions(tf.Tensor): The model's predictions for the input data
    """
    feature_spec = tf_transform_output.raw_feature_spec()
    feature_spec.pop(LABEL_KEY)

    parsed_features = tf.io.parse_example(serialized_tf_examples, feature_spec)
    transformed_features = model.tft_layer(parsed_features)
    predictions = model(transformed_features)

    return predictions

  return serve_tf_examples_fn

def run_fn(fn_args: FnArgs) -> None:
  """ Train the model based on given args

  Args:
    fn_args(FnArgs): Arguments provided by TFX, including:
      - train_files: List of training data files.
      - eval_files: List of evaluation data files.
      - transform_output: Output from the TFX transformation component.
      - train_steps: Number of training steps per epoch.
      - eval_steps: Number of evaluation steps per epoch.
      - serving_model_dir: Directory to save the trained model.
      - hyperparameters: Best hyperparameters from the tuner.
  """

  log_dir = os.path.join(os.path.dirname(fn_args.serving_model_dir), 'logs')

  tensorboard_callback = tf.keras.callbacks.TensorBoard(
      log_dir = log_dir, update_freq='batch'
  )

  early_stop = tf.keras.callbacks.EarlyStopping(monitor='val_binary_accuracy', mode='max', verbose=1, patience=10)
  model_checkpoint = tf.keras.callbacks.ModelCheckpoint(fn_args.serving_model_dir, monitor='val_binary_accuracy', mode='max', verbose=1, save_best_only=True)

  tf_transform_output = tft.TFTransformOutput(fn_args.transform_graph_path)

  train_set = input_fn(fn_args.train_files, tf_transform_output, 10)
  val_set = input_fn(fn_args.eval_files, tf_transform_output, 10)
  vectorize_layer.adapt(
      [j][0].numpy()[0] for j in [
          i[0][transformed_name(FEATURE_KEY)]
            for i in list(train_set)
      ]
  )

  model = model_builder()

  model.fit(
      x=train_set,
      validation_data=val_set,
      callbacks=[tensorboard_callback, early_stop, model_checkpoint],
      steps_per_epoch=200,
      validation_steps=200,
      epochs=10
  )

  signatures = {
      'serving_default':
      get_serve_tf_examples_fn(model, tf_transform_output).get_concrete_function(
          tf.TensorSpec(
              shape=[None],
              dtype=tf.string,
              name='examples'
          )
      )
  }

  print("Model will be saved to:", fn_args.serving_model_dir)
  model.save(fn_args.serving_model_dir, save_format='tf', signatures=signatures)


Overwriting modules/trainer.py


In [20]:
from tfx.proto import trainer_pb2

trainer = Trainer(
    module_file = os.path.abspath(TRAINER_MODULE_FILE),
    examples = transform.outputs['transformed_examples'],
    transform_graph = transform.outputs['transform_graph'],
    schema = schema_gen.outputs['schema'],
    train_args = trainer_pb2.TrainArgs(splits=['train']),
    eval_args = trainer_pb2.EvalArgs(splits=['eval'])
)
interactive_context.run(trainer)

Model: "model_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 text_xf (InputLayer)        [(None, 1)]               0         
                                                                 
 tf.reshape_1 (TFOpLambda)   (None,)                   0         
                                                                 
 text_vectorization_1 (Text  (None, 100)               0         
 Vectorization)                                                  
                                                                 
 embedding (Embedding)       (None, 100, 16)           160000    
                                                                 
 bidirectional_1 (Bidirecti  (None, 100, 128)          41472     
 onal)                                                           
                                                                 
 lstm_3 (LSTM)               (None, 64)                4940


Epoch 1: val_binary_accuracy improved from -inf to 0.94183, saving model to piplines/mushroom-pipline/Trainer/model/7/Format-Serving
200/200 [==============================] - 104s 484ms/step - loss: 0.3470 - binary_accuracy: 0.8500 - val_loss: 0.1902 - val_binary_accuracy: 0.9418
Epoch 2/10
200/200 [==============================] - ETA: 0s - loss: 0.1648 - binary_accuracy: 0.9446

200/200 [==============================] - 57s 286ms/step - loss: 0.1648 - binary_accuracy: 0.9446
Epoch 3/10
200/200 [==============================] - ETA: 0s - loss: 0.0237 - binary_accuracy: 0.9941

200/200 [==============================] - 56s 282ms/step - loss: 0.0237 - binary_accuracy: 0.9941
Epoch 4/10
113/200 [===============>..............] - ETA: 25s - loss: 0.0082 - binary_accuracy: 0.9989

200/200 [==============================] - 33s 165ms/step - loss: 0.0082 - binary_accuracy: 0.9989
Model will be saved to: piplines/mushroom-pipline/Trainer/model/7/Format-Serving


ExecutionResult(
    component_id: Trainer
    execution_id: 7
    outputs:
        model: OutputChannel(artifact_type=Model, producer_component_id=Trainer, output_key=model, additional_properties={}, additional_custom_properties={}, _input_trigger=None
        model_run: OutputChannel(artifact_type=ModelRun, producer_component_id=Trainer, output_key=model_run, additional_properties={}, additional_custom_properties={}, _input_trigger=None)

## Analisis dan Validasi Model

### Resolver

In [21]:
from tfx.dsl.components.common.resolver import Resolver
from tfx.dsl.input_resolution.strategies.latest_blessed_model_strategy import LatestBlessedModelStrategy
from tfx.types import Channel
from tfx.types.standard_artifacts import Model, ModelBlessing

model_resolver = Resolver(
    strategy_class=LatestBlessedModelStrategy,
    model=Channel(type=Model),
    model_blessing=Channel(type=ModelBlessing)
).with_id('Latest_blessed_model_resolver')

interactive_context.run(model_resolver)


ExecutionResult(
    component_id: Latest_blessed_model_resolver
    execution_id: 8
    outputs:
        model: OutputChannel(artifact_type=Model, producer_component_id=Latest_blessed_model_resolver, output_key=model, additional_properties={}, additional_custom_properties={}, _input_trigger=None
        model_blessing: OutputChannel(artifact_type=ModelBlessing, producer_component_id=Latest_blessed_model_resolver, output_key=model_blessing, additional_properties={}, additional_custom_properties={}, _input_trigger=None)

## Evaluator

In [24]:
import tensorflow_model_analysis as tfma

eval_config = tfma.EvalConfig(
    model_specs=[tfma.ModelSpec(label_key='spam')],
    slicing_specs=[tfma.SlicingSpec()],
    metrics_specs=[
        tfma.MetricsSpec(metrics=[
            tfma.MetricConfig(class_name='ExampleCount'),
            tfma.MetricConfig(class_name='AUC'),
            tfma.MetricConfig(class_name='FalsePositives'),
            tfma.MetricConfig(class_name='TruePositives'),
            tfma.MetricConfig(class_name='FalseNegatives'),
            tfma.MetricConfig(class_name='TrueNegatives'),
            tfma.MetricConfig(class_name='BinaryAccuracy',
            threshold=tfma.MetricThreshold(
                    value_threshold=tfma.GenericValueThreshold(
                        lower_bound={'value':0.5}),
                    change_threshold=tfma.GenericChangeThreshold(
                        direction=tfma.MetricDirection.HIGHER_IS_BETTER,
                        absolute={'value':0.0001}))
            )
        ])
    ]
)

In [25]:
from tfx.components import Evaluator
evaluator = Evaluator(
    examples=example_gen.outputs['examples'],
    model=trainer.outputs['model'],
    baseline_model=model_resolver.outputs['model'],
    eval_config=eval_config
)

interactive_context.run(evaluator)

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


ExecutionResult(
    component_id: Evaluator
    execution_id: 10
    outputs:
        evaluation: OutputChannel(artifact_type=ModelEvaluation, producer_component_id=Evaluator, output_key=evaluation, additional_properties={}, additional_custom_properties={}, _input_trigger=None
        blessing: OutputChannel(artifact_type=ModelBlessing, producer_component_id=Evaluator, output_key=blessing, additional_properties={}, additional_custom_properties={}, _input_trigger=None)

## Deployment

### Pusher

In [26]:
from tfx.components import Pusher
from tfx.proto import pusher_pb2

pusher = Pusher(
    model = trainer.outputs['model'],
    model_blessing = evaluator.outputs['blessing'],
    push_destination = pusher_pb2.PushDestination(
        filesystem = pusher_pb2.PushDestination.Filesystem(
            base_directory = 'serving_model_dir/email-classification-model'
        )
    )
)

interactive_context.run(pusher)

ExecutionResult(
    component_id: Pusher
    execution_id: 11
    outputs:
        pushed_model: OutputChannel(artifact_type=PushedModel, producer_component_id=Pusher, output_key=pushed_model, additional_properties={}, additional_custom_properties={}, _input_trigger=None)

In [ ]:
!zip -r /content/all_files.zip /content -x "/content/.config/*" "/content/.ipynb_checkpoints/*" "/content/sample_data/*"